## Business Problem

Melbourne has been voted the most livable city in the World for seven years in a row, which attract a lot of families or individuals to migrate to Melbourne. The question / problem comes in deciding where to step foot in Melbourne, which suburb to live in. For many young families the priority is to provide best possible education to their children at an affordable price. In addition to good schools, the presence of other basic amenities is also important ( Transport, Hospitals, Resturants and others)
In this project the objective is to select top 10 Public Primary and Secondary Schools. List all the amenities for the corresponding suburbs where the schools are located  with the median rent in the area so that the user be able to make a decision of selecting a suburb to settle down.

## Data Set

In order to carry out the investigation and determining the most suitable Suburb, we need access to certain information. This information can be retiereived from the Data available at various sites and consolidated and evaluated to reach to the conclusion

Data Set can be obtained from the following sites

1> List of Melbourne Suburbs and Postcodes - https://en.wikipedia.org/wiki/List_of_Melbourne_suburbs  
2> List of Top Public School in Melbourne - https://bettereducation.com.au/school  
3> List of Facilities from Foursquare  
4> Housing Information from Real Estate sites

Before we get the data and start exploring it, let's download all the dependencies that we will need.

In [2]:
from bs4 import BeautifulSoup

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files
import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

import lxml.html as lh
import numpy as np

!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

Fetching package metadata .............
Solving package specifications: .

# All requested packages already installed.
# packages in environment at /opt/conda/envs/DSX-Python35:
#
geopy                     1.18.1                     py_0    conda-forge
Fetching package metadata .............
Solving package specifications: .

# All requested packages already installed.
# packages in environment at /opt/conda/envs/DSX-Python35:
#
folium                    0.5.0                      py_0    conda-forge


## 1. Download and Explore Dataset

#### Load and explore the data

Next, let's load the data.

In [3]:
## Connecting to the Url and Checking the status
response = requests.get("https://www.costlessquotes.com.au/postcode_tool/postcode_list_VIC.php")
response.status_code

200

In [4]:
## Using Pandas and BeautifulSoup to Parse Table from the site

soup = BeautifulSoup(response.content,'html.parser')

table = soup.find_all('table')
table = table[0]

## Initialise empty column header list and df list
columns_headers = []
df = []

## Capture the column headings from the table

for row in table.find_all('tr'):
    for cell in row.find_all('th'):
        columns_headers.append(cell.text.strip())
        
## Capture the table rows data

for tr in table.find_all('tr'):
    td = tr.find_all('td')
    row = [tr.text.strip() for tr in td if tr.text.strip()]
    if row:
        df.append(row)
        
victoria_data = pd.DataFrame(df,columns = columns_headers)
victoria_data.head()

Postcode   District       City/ Town/ Suburb
0     3000  Melbourne                Melbourne
1     3001  Melbourne                Melbourne
2     3002  Melbourne           East Melbourne
3     3003  Melbourne           West Melbourne
4     3004  Melbourne  St Kilda Road Melbourne

In [5]:
## Uploading GeoCordinates for Victoria ( Australia) via csv file

import types
import pandas as pd
from botocore.client import Config
import ibm_boto3

def __iter__(self): return 0

# @hidden_cell
# The following code accesses a file in your IBM Cloud Object Storage. It includes your credentials.
# You might want to remove those credentials before you share your notebook.
client_391bf9c3d6dd49539d901e1c6c7fc867 = ibm_boto3.client(service_name='s3',
    ibm_api_key_id='CfF_o5dcsFBLGj_k9t8AlZMtfN5OhM0IqTuTZiKXeWEL',
    ibm_auth_endpoint="https://iam.bluemix.net/oidc/token",
    config=Config(signature_version='oauth'),
    endpoint_url='https://s3-api.us-geo.objectstorage.service.networklayer.com')

body = client_391bf9c3d6dd49539d901e1c6c7fc867.get_object(Bucket='courseracapstone-donotdelete-pr-du7ip5uai7v1u7',Key='Postcodes_GeoCordinates.csv')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )

df_GeoCordinates = pd.read_csv(body)
df_GeoCordinates.columns = ['Postcode','Suburb','State','Lat','Long']
df_GeoCordinates['Postcode']=df_GeoCordinates['Postcode'].apply(str)
df_GeoCordinates.drop_duplicates(subset=['Suburb'],inplace=True)
df_GeoCordinates.head()

Postcode    Suburb State    Lat    Long
0      221    Barton   ACT -35.20  149.10
1      800    Darwin    NT -12.80  130.96
3      804     Parap    NT -12.43  130.84
4      810     Alawa    NT -12.38  130.88
5      810   Brinkin    NT -12.38  130.88

In [6]:
## Merging dataframe to create Postcode Dataframe with Geocordinates

victoria_data = pd.merge(victoria_data,df_GeoCordinates, how='inner',on = ['Postcode'])
victoria_data=victoria_data.drop(['City/ Town/ Suburb'],axis=1)

print('Victoria has {} District and {} Suburbs.'.format(
        len(victoria_data['District'].unique()),
        victoria_data.shape[0]
    )
)
victoria_data.head()

Victoria has 12 District and 2919 Suburbs.


Postcode   District                  Suburb State    Lat    Long
0     3000  Melbourne               Melbourne   VIC -37.81  144.97
1     3002  Melbourne          East Melbourne   VIC -37.82  144.99
2     3003  Melbourne          West Melbourne   VIC -37.81  144.94
3     3004  Melbourne   St Kilda Road Central   VIC -37.84  144.98
4     3005  Melbourne      World Trade Centre   VIC -37.82  144.95

In [7]:
## Creating Dataframe for Melbourne District 

melbourne_data=victoria_data[victoria_data['District']=='Melbourne']
melbourne_data = melbourne_data.drop(melbourne_data[melbourne_data.Lat == 0].index)
print(melbourne_data.tail())
melbourne_data.shape

     Postcode   District            Suburb State    Lat    Long
2863     3977  Melbourne              Skye   VIC -38.21  145.32
2914     8004  Melbourne     St Kilda Road   VIC -37.84  144.98
2915     8006  Melbourne   Abeckett Street   VIC -37.81  144.96
2917     8009  Melbourne     Flinders Lane   VIC -37.82  144.96
2918     8010  Melbourne        Law Courts   VIC -38.19  146.29


(558, 6)

In [8]:
address = 'Melbourne,Australia'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of {} are {}, {}.'.format(address,latitude, longitude))

/opt/conda/envs/DSX-Python35/lib/python3.5/site-packages/ipykernel/__main__.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.18.1" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  app.launch_new_instance()


The geograpical coordinate of Melbourne,Australia are -37.8142176, 144.9631608.


#### Create a map of Melbourne with Suburbs superimposed on top.

In [9]:
# create map of Manhattan using latitude and longitude values
map_melbourne = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, District, suburb, Postcode in zip(melbourne_data['Lat'], melbourne_data['Long'], melbourne_data['Suburb'], melbourne_data['District'],melbourne_data['Postcode']):
    label = '{},{},{}'.format(District,suburb,Postcode)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_melbourne)  
    
map_melbourne

#### Define Foursquare Credentials and Version

In [10]:
CLIENT_ID = 'FOTGONFCMLBWW0D3HHTFQ3ERRJWJ33UWLY2F0I2LYHSQ0WWY' # your Foursquare ID
CLIENT_SECRET = '1F4LGDXKI4S3ZJ4VHDRIQNNRPSHLOHO1SEFUHZX4WYZUYFYF' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: FOTGONFCMLBWW0D3HHTFQ3ERRJWJ33UWLY2F0I2LYHSQ0WWY
CLIENT_SECRET:1F4LGDXKI4S3ZJ4VHDRIQNNRPSHLOHO1SEFUHZX4WYZUYFYF


#### Let's explore the first neighborhood in our dataframe.

In [11]:
melbourne_data.loc[0, 'Suburb']

' Melbourne'

Get the neighborhood's latitude and longitude values.

In [12]:
neighborhood_latitude = melbourne_data.loc[0, 'Lat'] # neighborhood latitude value
neighborhood_longitude = melbourne_data.loc[0, 'Long'] # neighborhood longitude value

neighborhood_name = melbourne_data.loc[0, 'Suburb'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of  Melbourne are -37.81, 144.97.


First, let's create the GET request URL. Name your URL **url**.

In [13]:
LIMIT=100
radius=500
url='http://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
   CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url

'http://api.foursquare.com/v2/venues/explore?client_id=FOTGONFCMLBWW0D3HHTFQ3ERRJWJ33UWLY2F0I2LYHSQ0WWY&client_secret=1F4LGDXKI4S3ZJ4VHDRIQNNRPSHLOHO1SEFUHZX4WYZUYFYF&v=20180605&ll=-37.81,144.97&radius=500&limit=100'

In [14]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5c5e39176a60712d31ca1e70'},
 'response': {'groups': [{'items': [{'reasons': {'count': 0,
       'items': [{'reasonName': 'globalInteractionReason',
         'summary': 'This spot is popular',
         'type': 'general'}]},
      'referralId': 'e-0-4d9e49d4a4675481aa278be6-0',
      'venue': {'categories': [{'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/coffeeshop_',
          'suffix': '.png'},
         'id': '4bf58dd8d48988d1e0931735',
         'name': 'Coffee Shop',
         'pluralName': 'Coffee Shops',
         'primary': True,
         'shortName': 'Coffee Shop'}],
       'id': '4d9e49d4a4675481aa278be6',
       'location': {'address': '8 Exploration Ln.',
        'cc': 'AU',
        'city': 'Melbourne',
        'country': 'Australia',
        'crossStreet': 'at Little Lonsdale St.',
        'distance': 155,
        'formattedAddress': ['8 Exploration Ln. (at Little Lonsdale St.)',
         'Melbourne VIC 3000',
         'Aust

In [15]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [16]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name        categories        lat         lng
0  The League of Honest Coffee       Coffee Shop -37.809279  144.968483
1                    Gingerboy  Asian Restaurant -37.811223  144.970982
2                    Traveller       Coffee Shop -37.811391  144.971232
3    Longrain Restaurant & Bar   Thai Restaurant -37.810733  144.971147
4               Rice Papr Scrs  Asian Restaurant -37.811298  144.971311

In [17]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

100 venues were returned by Foursquare.


## 2. Explore Neighborhoods in Melbourne

In [18]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()['response']['groups'][0]['items']
        
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])
        
    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Suburb', 
                  'Suburb Latitude', 
                  'Suburb Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)


In [19]:
# Melbourne Venues by Suburbs
melbourne_venues = getNearbyVenues(names=melbourne_data['Suburb'],
                                   latitudes=melbourne_data['Lat'],
                                   longitudes=melbourne_data['Long']
                                  )

 Melbourne
 East Melbourne
 West Melbourne
 St Kilda Road Central
 World Trade Centre
 South Wharf
 Southbank
 Docklands
 University Of Melbourne
 Footscray
 Seddon
 Seddon West
 Kingsville
 Kingsville West
 Maidstone
 West Footscray
 Yarraville
 Yarraville West
 South Kingsville
 Spotswood
 Williamstown
 Williamstown North
 Altona
 Seaholme
 Braybrook
 Braybrook North
 Robinson
 Albion
 Glengala
 Sunshine North
 Sunshine West
 Albanvale
 Kealba
 Ardeer
 Deer Park East
 Burnside
 Burnside Heights
 Cairnlea
 Caroline Springs
 Deer Park
 Deer Park North
 Ravenhall
 Mambourin
 Mount Cottrell
 Wyndham Vale
 Altona East
 Altona Gate
 Altona North
 Laverton North
 Williams Landing
 Altona Meadows
 Laverton
 Seabrook
 Hoppers Crossing
 Tarneit
 Truganina
 Cocoroc
 Derrimut
 Point Cook
 Quandong
 Werribee
 Werribee South
 Flemington
 Ascot Vale
 Highpoint City
 Maribyrnong
 Travancore
 Keilor East
 Avondale Heights
 Keilor
 Keilor North
 Calder Park
 Delahey
 Hillside
 Taylors Hill
 Keilor Dow

In [20]:
print(melbourne_venues.shape)
melbourne_venues.head()

(6344, 7)


Suburb  Suburb Latitude  Suburb Longitude                        Venue  \
0   Melbourne           -37.81            144.97  The League of Honest Coffee   
1   Melbourne           -37.81            144.97                    Gingerboy   
2   Melbourne           -37.81            144.97                    Traveller   
3   Melbourne           -37.81            144.97    Longrain Restaurant & Bar   
4   Melbourne           -37.81            144.97               Rice Papr Scrs   

   Venue Latitude  Venue Longitude    Venue Category  
0      -37.809279       144.968483       Coffee Shop  
1      -37.811223       144.970982  Asian Restaurant  
2      -37.811391       144.971232       Coffee Shop  
3      -37.810733       144.971147   Thai Restaurant  
4      -37.811298       144.971311  Asian Restaurant

In [21]:
melbourne_venues.groupby('Suburb').count()

Suburb Latitude  Suburb Longitude  Venue  \
Suburb                                                                
 Abeckett Street                       100               100    100   
 Aberfeldie                              1                 1      1   
 Airport West                            8                 8      8   
 Albanvale                               4                 4      4   
 Albert Park                            33                33     33   
 Albion                                  2                 2      2   
 Alphington                              6                 6      6   
 Altona                                 12                12     12   
 Altona East                             4                 4      4   
 Altona Gate                             4                 4      4   
 Altona Meadows                          8                 8      8   
 Altona North                            4                 4      4   
 Ardeer                                  2                 2      2   
 Armadale                               10                10     10   
 Armadale North                         10                10     10   
 Arthurs Seat                            4                 4      4   
 Ascot Vale                             14                14     14   
 Ashburton                              12                12     12   
 Ashwood                                12                12     12   
 Aspendale                               6                 6      6   
 Aspendale Gardens                       6                 6      6   
 Attwood                                 4                 4      4   
 Auburn South                            4                 4      4   
 Avondale Heights                        3                 3      3   
 Avonsleigh                              5                 5      5   
 Badger Creek                            1                 1      1   
 Balaclava                              11                11     11   
 Balnarring                              3                 3      3   
 Balnarring Beach                        3                 3      3   
 Balwyn                                 18                18     18   
 Balwyn East                            18                18     18   
 Balwyn North                            5                 5      5   
 Bangholme                               1                 1      1   
 Banyule                                 1                 1      1   
 Batman                                  7                 7      7   
 Baxter                                  1                 1      1   
 Bayswater                              14                14     14   
 Bayswater North                        14                14     14   
 Beaconsfield Upper                      3                 3      3   
 Beaumaris                               4                 4      4   
 Bedford Road                            2                 2      2   
 Belgrave                               11                11     11   
 Belgrave Heights                       11                11     11   
 Belgrave South                         11                11     11   
 Bellfield                               4                 4      4   
 Belvedere Park                         14                14     14   
 Bennettswood                            4                 4      4   
 Bentleigh                              26                26     26   
 Bentleigh East                          6                 6      6   
 Berwick                                 5                 5      5   
 Bittern                                 4                 4      4   
 Black Rock                              4                 4      4   
 Black Rock North                        4                 4      4   
 Blackburn                              17                17     17   
 Blackburn North                        17         

In [23]:
print('There are {} uniques categories.'.format(len(melbourne_venues['Venue Category'].unique())))

There are 282 uniques categories.


## 3. Analyze Each Suburb

In [25]:
# one hot encoding
melbourne_onehot = pd.get_dummies(melbourne_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
melbourne_onehot['Suburb'] = melbourne_venues['Suburb'] 

# move neighborhood column to the first column
fixed_columns = [melbourne_onehot.columns[-1]] + list(melbourne_onehot.columns[:-1])
melbourne_onehot = melbourne_onehot[fixed_columns]

melbourne_onehot.head()

Suburb  African Restaurant  Airport Service  Antique Shop  Aquarium  \
0   Melbourne                   0                0             0         0   
1   Melbourne                   0                0             0         0   
2   Melbourne                   0                0             0         0   
3   Melbourne                   0                0             0         0   
4   Melbourne                   0                0             0         0   

   Arcade  Argentinian Restaurant  Art Gallery  Arts & Crafts Store  \
0       0                       0            0                    0   
1       0                       0            0                    0   
2       0                       0            0                    0   
3       0                       0            0                    0   
4       0                       0            0                    0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  \
0                     0                 0                   0   
1                     0                 1                   0   
2                     0                 0                   0   
3                     0                 0                   0   
4                     0                 1                   0   

   Australian Restaurant  Auto Garage  BBQ Joint  Bagel Shop  Bakery  Bar  \
0                      0            0          0           0       0    0   
1                      0            0          0           0       0    0   
2                      0            0          0           0       0    0   
3                      0            0          0           0       0    0   
4                      0            0          0           0       0    0   

   Baseball Field  Basketball Court  Beach  Bed & Breakfast  Beer Bar  \
0               0                 0      0                0         0   
1               0                 0      0                0         0   
2               0                 0      0                0         0   
3               0                 0      0                0         0   
4               0                 0      0                0         0   

   Beer Garden  Big Box Store  Bike Rental / Bike Share  Bistro  Bookstore  \
0            0              0                         0       0          0   
1            0              0                         0       0          0   
2            0              0                         0       0          0   
3            0              0                         0       0          0   
4            0              0                         0       0          0   

   Boutique  Bowling Alley  Bowling Green  Boxing Gym  Breakfast Spot  \
0         0              0              0           0               0   
1         0              0              0           0               0   
2         0              0              0           0               0   
3         0              0              0           0               0   
4         0              0              0           0               0   

   Brewery  Bubble Tea Shop  Building  Burger Joint  Burrito Place  \
0        0                0         0             0              0   
1        0                0         0             0              0   
2        0                0         0             0              0   
3        0                0         0             0              0   
4        0                0         0             0              0   

   Bus Station  Bus Stop  Business Service  Butcher  Cable Car  Café  \
0            0         0                 0        0          0     0   
1            0         0                 0        0          0     0   
2            0         0                 0        0          0     0   
3            0         0                 0        0          0     0   
4            0         0                 0        0          0     0   

   Camera Store  Candy Store  Car Wash  Carpet Store  Ca

In [26]:
melbourne_onehot.shape

(6344, 283)

In [28]:
melbourne_grouped = melbourne_onehot.groupby('Suburb').mean().reset_index()
melbourne_grouped

Suburb  African Restaurant  Airport Service  \
0              Abeckett Street                0.00              0.0   
1                   Aberfeldie                0.00              0.0   
2                 Airport West                0.00              0.0   
3                    Albanvale                0.00              0.0   
4                  Albert Park                0.00              0.0   
5                       Albion                0.00              0.0   
6                   Alphington                0.00              0.0   
7                       Altona                0.00              0.0   
8                  Altona East                0.00              0.0   
9                  Altona Gate                0.00              0.0   
10              Altona Meadows                0.00              0.0   
11                Altona North                0.00              0.0   
12                      Ardeer                0.00              0.0   
13                    Armadale                0.00              0.0   
14              Armadale North                0.00              0.0   
15                Arthurs Seat                0.00              0.0   
16                  Ascot Vale                0.00              0.0   
17                   Ashburton                0.00              0.0   
18                     Ashwood                0.00              0.0   
19                   Aspendale                0.00              0.0   
20           Aspendale Gardens                0.00              0.0   
21                     Attwood                0.00              0.0   
22                Auburn South                0.00              0.0   
23            Avondale Heights                0.00              0.0   
24                  Avonsleigh                0.00              0.0   
25                Badger Creek                0.00              0.0   
26                   Balaclava                0.00              0.0   
27                  Balnarring                0.00              0.0   
28            Balnarring Beach                0.00              0.0   
29                      Balwyn                0.00              0.0   
30                 Balwyn East                0.00              0.0   
31                Balwyn North                0.00              0.0   
32                   Bangholme                0.00              0.0   
33                     Banyule                0.00              0.0   
34                      Batman                0.00              0.0   
35                      Baxter                0.00              0.0   
36                   Bayswater                0.00              0.0   
37             Bayswater North                0.00              0.0   
38          Beaconsfield Upper                0.00              0.0   
39                   Beaumaris                0.00              0.0   
40                Bedford Road                0.00              0.0   
41                    Belgrave                0.00              0.0   
42            Belgrave Heights                0.00              0.0   
43              Belgrave South                0.00              0.0   
44                   Bellfield                0.00              0.0   
45              Belvedere Park                0.00              0.0   
46                Bennettswood                0.00              0.0   
47                   Bentleigh                0.00              0.0   
48              Bentleigh East                0.00              0.0   
49                     Berwick                0.00              0.0   
50                     Bittern                0.00              0.0   
51                  Black Rock                0.00              0.0   
52            Black Rock North                0.00              0.0   
53                   Blackburn                0.00              0.0   
54             Blackburn North                0.00              0.0   
55             Blackburn South                0.

In [29]:
melbourne_grouped.shape

(488, 283)

#### Let's print each Subrub along with the top 5 most common venues

In [30]:
num_top_venues = 5

for hood in melbourne_grouped['Suburb']:
    print("----"+hood+"----")
    temp = melbourne_grouped[melbourne_grouped['Suburb'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

---- Abeckett Street----
                 venue  freq
0                 Café  0.13
1    Korean Restaurant  0.09
2          Coffee Shop  0.07
3                  Bar  0.06
4  Japanese Restaurant  0.03


---- Aberfeldie----
                venue  freq
0  Athletics & Sports   1.0
1  African Restaurant   0.0
2         Pizza Place   0.0
3                Pier   0.0
4  Physical Therapist   0.0


---- Airport West----
                   venue  freq
0   Fast Food Restaurant  0.12
1  Portuguese Restaurant  0.12
2       Department Store  0.12
3         Sandwich Place  0.12
4     Light Rail Station  0.12


---- Albanvale----
                           venue  freq
0                    Supermarket  0.50
1                 Discount Store  0.25
2               Video Game Store  0.25
3  Paper / Office Supplies Store  0.00
4             Physical Therapist  0.00


---- Albert Park----
                venue  freq
0                Café  0.12
1  Light Rail Station  0.12
2  Athletics & Sports  0.09
3          

                  venue  freq
0                  Café  0.50
1  Fast Food Restaurant  0.25
2  Gym / Fitness Center  0.25
3      Pedestrian Plaza  0.00
4                  Pier  0.00


---- Belvedere Park----
                  venue  freq
0         Grocery Store  0.21
1  Fast Food Restaurant  0.14
2           Pizza Place  0.14
3        Sandwich Place  0.07
4                   Pub  0.07


---- Bennettswood----
                venue  freq
0         Golf Course  0.50
1                Park  0.25
2               Motel  0.25
3        Noodle House  0.00
4  Physical Therapist  0.00


---- Bentleigh----
                  venue  freq
0                  Café  0.19
1                Bakery  0.12
2   Japanese Restaurant  0.08
3      Department Store  0.04
4  Gym / Fitness Center  0.04


---- Bentleigh East----
          venue  freq
0      Bus Stop  0.17
1          Café  0.17
2    Playground  0.17
3          Park  0.17
4  Tennis Court  0.17


---- Berwick----
                venue  freq
0  Mexican Resta

                venue  freq
0                Park  0.25
1          Playground  0.25
2           BBQ Joint  0.25
3         Golf Course  0.25
4  African Restaurant  0.00


---- Camberwell North----
                venue  freq
0               Train   0.2
1            Pharmacy   0.2
2   Convenience Store   0.2
3  Light Rail Station   0.2
4        Liquor Store   0.2


---- Camberwell South----
                venue  freq
0               Train   0.2
1            Pharmacy   0.2
2   Convenience Store   0.2
3  Light Rail Station   0.2
4        Liquor Store   0.2


---- Camberwell West----
                venue  freq
0               Train   0.2
1            Pharmacy   0.2
2   Convenience Store   0.2
3  Light Rail Station   0.2
4        Liquor Store   0.2


---- Campbellfield----
           venue  freq
0   Dessert Shop  0.12
1    Auto Garage  0.12
2    Music Store  0.12
3  Grocery Store  0.12
4       Gun Shop  0.12


---- Carlton North----
                venue  freq
0                Café  0.08
1

                  venue  freq
0  Fast Food Restaurant  0.20
1      Department Store  0.10
2        Sandwich Place  0.10
3           Supermarket  0.10
4      Basketball Court  0.05


---- Dandenong----
                venue  freq
0        Carpet Store   1.0
1  African Restaurant   0.0
2    Pedestrian Plaza   0.0
3                Pier   0.0
4  Physical Therapist   0.0


---- Dandenong East----
                venue  freq
0        Carpet Store   1.0
1  African Restaurant   0.0
2    Pedestrian Plaza   0.0
3                Pier   0.0
4  Physical Therapist   0.0


---- Dandenong North----
                venue  freq
0        Carpet Store   1.0
1  African Restaurant   0.0
2    Pedestrian Plaza   0.0
3                Pier   0.0
4  Physical Therapist   0.0


---- Dandenong Plaza----
                venue  freq
0        Carpet Store   1.0
1  African Restaurant   0.0
2    Pedestrian Plaza   0.0
3                Pier   0.0
4  Physical Therapist   0.0


---- Dandenong South----
             venue  

                   venue  freq
0                   Café  0.17
1                    Pub  0.07
2            Pizza Place  0.07
3  Vietnamese Restaurant  0.05
4       Malay Restaurant  0.05


---- Flinders Lane----
                 venue  freq
0                  Bar  0.10
1                 Café  0.10
2          Coffee Shop  0.08
3  Japanese Restaurant  0.06
4   Italian Restaurant  0.05


---- Footscray----
                   venue  freq
0  Vietnamese Restaurant  0.19
1                   Café  0.15
2       Asian Restaurant  0.10
3        Bubble Tea Shop  0.04
4                    Bar  0.04


---- Fountain Gate----
                  venue  freq
0  Fast Food Restaurant  0.15
1      Department Store  0.10
2                  Café  0.08
3     Electronics Store  0.05
4                Arcade  0.03


---- Frankston----
       venue  freq
0      Beach  0.38
1      Field  0.12
2    Theater  0.12
3       Park  0.12
4  Hotel Bar  0.12


---- Frankston East----
       venue  freq
0      Beach  0.38
1   

...

                           venue  freq
0                  Garden Center   1.0
1  Paper / Office Supplies Store   0.0
2             Physical Therapist   0.0
3                       Pharmacy   0.0
4                      Pet Store   0.0


---- Mont Albert----
                   venue  freq
0                   Café  0.18
1           Burger Joint  0.18
2  Australian Restaurant  0.09
3          Grocery Store  0.09
4        Thai Restaurant  0.09


---- Mont Albert North----
                venue  freq
0                Park  0.17
1        Dance Studio  0.17
2  Italian Restaurant  0.17
3              Bakery  0.17
4            Pharmacy  0.17


---- Montmorency----
                venue  freq
0                Café  0.33
1     Thai Restaurant  0.17
2        Burger Joint  0.17
3  Chinese Restaurant  0.17
4       Grocery Store  0.17


---- Montrose----
                  venue  freq
0  Fast Food Restaurant   0.2
1                  Café   0.2
2                Bakery   0.2
3        Sandwich Place   0.2

                           venue  freq
0                Warehouse Store  0.33
1                           Café  0.33
2                    Video Store  0.33
3  Paper / Office Supplies Store  0.00
4             Physical Therapist  0.00


---- Oakleigh South----
                    venue  freq
0       Health Food Store   0.2
1  Furniture / Home Store   0.2
2       Other Repair Shop   0.2
3       Convenience Store   0.2
4             Golf Course   0.2


---- Officer----
                           venue  freq
0                    Gas Station  0.33
1  Paper / Office Supplies Store  0.33
2                           Café  0.33
3             Physical Therapist  0.00
4                       Pharmacy  0.00


---- Officer South----
                           venue  freq
0                    Gas Station  0.33
1  Paper / Office Supplies Store  0.33
2                           Café  0.33
3             Physical Therapist  0.00
4                       Pharmacy  0.00


---- Ormond----
                  

                  venue  freq
0  Gym / Fitness Center  0.23
1            Restaurant  0.08
2   Arts & Crafts Store  0.08
3                   Gym  0.08
4         Shopping Mall  0.08


---- Rosanna----
                           venue  freq
0                   Tennis Court   1.0
1             African Restaurant   0.0
2  Paper / Office Supplies Store   0.0
3             Physical Therapist   0.0
4                       Pharmacy   0.0


---- Rowville----
                  venue  freq
0           IT Services   0.5
1  Fast Food Restaurant   0.5
2    African Restaurant   0.0
3                  Park   0.0
4                  Pier   0.0


---- Roxburgh Park----
                venue  freq
0  Chinese Restaurant  0.12
1                 Gym  0.12
2  Italian Restaurant  0.12
3       Train Station  0.12
4       Shopping Mall  0.12


---- Royal Melbourne Hospital----
               venue  freq
0               Café  0.26
1        Coffee Shop  0.06
2        Pizza Place  0.06
3  Indian Restaurant  0.04
4  

                      venue  freq
0                      Park  0.43
1               Pizza Place  0.14
2               Golf Course  0.14
3  Bike Rental / Bike Share  0.14
4        Light Rail Station  0.14


---- Sunbury----
                  venue  freq
0                  Café  0.17
1  Fast Food Restaurant  0.12
2         Grocery Store  0.12
3            Restaurant  0.08
4      Video Game Store  0.04


---- Sunshine North----
                venue  freq
0       Train Station   0.5
1                Park   0.5
2           Nightclub   0.0
3                Pier   0.0
4  Physical Therapist   0.0


---- Sunshine West----
                venue  freq
0       Train Station   0.5
1                Park   0.5
2           Nightclub   0.0
3                Pier   0.0
4  Physical Therapist   0.0


---- Surrey Hills----
                   venue  freq
0                   Café  0.18
1           Burger Joint  0.18
2  Australian Restaurant  0.09
3          Grocery Store  0.09
4        Thai Restaurant  0.09


                venue  freq
0                Park  0.33
1        Hockey Field  0.33
2           Wine Shop  0.33
3  African Restaurant  0.00
4                Pier  0.00


---- Were Street Po----
                   venue  freq
0                   Café  0.21
1  Australian Restaurant  0.14
2           Burger Joint  0.07
3              Bookstore  0.07
4          Movie Theater  0.07


---- West Footscray----
                           venue  freq
0                  Women's Store   1.0
1             African Restaurant   0.0
2  Paper / Office Supplies Store   0.0
3             Physical Therapist   0.0
4                       Pharmacy   0.0


---- West Melbourne----
            venue  freq
0            Café  0.12
1   Shopping Mall  0.08
2     Men's Store  0.04
3  Sandwich Place  0.04
4    Skating Rink  0.04


---- Westmeadows----
                venue  freq
0               Motel  0.75
1          Restaurant  0.25
2  Physical Therapist  0.00
3            Pharmacy  0.00
4           Pet Store  0.00

In [31]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [32]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Suburb']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
Suburb_venues_sorted = pd.DataFrame(columns=columns)
Suburb_venues_sorted['Suburb'] = melbourne_grouped['Suburb']

for ind in np.arange(melbourne_grouped.shape[0]):
    Suburb_venues_sorted.iloc[ind, 1:] = return_most_common_venues(melbourne_grouped.iloc[ind, :], num_top_venues)

Suburb_venues_sorted

Suburb          1st Most Common Venue  \
0              Abeckett Street                           Café   
1                   Aberfeldie             Athletics & Sports   
2                 Airport West          Portuguese Restaurant   
3                    Albanvale                    Supermarket   
4                  Albert Park                           Café   
5                       Albion                  Train Station   
6                   Alphington           Gym / Fitness Center   
7                       Altona             Italian Restaurant   
8                  Altona East           Gym / Fitness Center   
9                  Altona Gate           Gym / Fitness Center   
10              Altona Meadows           Fast Food Restaurant   
11                Altona North           Gym / Fitness Center   
12                      Ardeer                  Train Station   
13                    Armadale                           Café   
14              Armadale North                           Café   
15                Arthurs Seat                 Scenic Lookout   
16                  Ascot Vale             Light Rail Station   
17                   Ashburton                           Café   
18                     Ashwood                           Café   
19                   Aspendale                           Café   
20           Aspendale Gardens                           Café   
21                     Attwood                          Motel   
22                Auburn South                           Park   
23            Avondale Heights                    Pizza Place   
24                  Avonsleigh             Italian Restaurant   
25                Badger Creek                         Winery   
26                   Balaclava            Japanese Restaurant   
27                  Balnarring                    Pizza Place   
28            Balnarring Beach                    Pizza Place   
29                      Balwyn                           Café   
30                 Balwyn East                           Café   
31                Balwyn North                           Café   
32                   Bangholme                   Carpet Store   
33                     Banyule                   Tennis Court   
34                      Batman             Light Rail Station   
35                      Baxter                      Gastropub   
36                   Bayswater                    Supermarket   
37             Bayswater North                    Supermarket   
38          Beaconsfield Upper                     Steakhouse   
39                   Beaumaris                Harbor / Marina   
40                Bedford Road                           Park   
41                    Belgrave                           Café   
42            Belgrave Heights                           Café   
43              Belgrave South                           Café   
44                   Bellfield                           Café   
45              Belvedere Park                  Grocery Store   
46                Bennettswood                    Golf Course   
47                   Bentleigh                           Café   
48              Bentleigh East             Italian Restaurant   
49                     Berwick                         Garden   
50                     Bittern                     Restaurant   
51                  Black Rock                Harbor / Marina   
52            Black Rock North                Harbor / Marina   
53                   Blackburn                           Café   
54             Blackburn North                           Café   
55             Blackburn South                           Café   
56                 Blairgowrie                Harbor / Marina   
57                    Bonbeach                  Deli / Bodega   
58              Booran Road Po                           Café   
59                     Boronia                  Grocery Store   
60            Box Hill Central             Chinese Restaura

## 4. Cluster Suburbs

In [41]:
# set number of clusters
kclusters = 5

melbourne_grouped_clustering = melbourne_grouped.drop('Suburb', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(melbourne_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 4, 0, 0, 0, 2, 0, 0, 0, 0], dtype=int32)

In [38]:
melbourne_data.shape

(558, 6)

In [39]:
Suburb_venues_sorted.shape

(488, 11)

In [43]:
melbourne_merged = melbourne_data[:488]

# add clustering labels
melbourne_merged['Cluster Labels'] = kmeans.labels_

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
melbourne_merged = melbourne_merged.join(Suburb_venues_sorted.set_index('Suburb'), on='Suburb')

melbourne_merged.head() # check the last columns!

/opt/conda/envs/DSX-Python35/lib/python3.5/site-packages/ipykernel/__main__.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


Postcode   District                  Suburb State    Lat    Long  \
0     3000  Melbourne               Melbourne   VIC -37.81  144.97   
1     3002  Melbourne          East Melbourne   VIC -37.82  144.99   
2     3003  Melbourne          West Melbourne   VIC -37.81  144.94   
3     3004  Melbourne   St Kilda Road Central   VIC -37.84  144.98   
4     3005  Melbourne      World Trade Centre   VIC -37.82  144.95   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0               0          Cocktail Bar                   Bar   
1               4                   Pub                  Café   
2               0                  Café         Shopping Mall   
3               0                  Café                 Hotel   
4               0                  Café                   Bar   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0           Coffee Shop              Wine Bar                  Café   
1           Coffee Shop        Breakfast Spot       Thai Restaurant   
2             Pool Hall         Grocery Store          Burger Joint   
3           Pizza Place    Light Rail Station     Indian Restaurant   
4           Coffee Shop       Thai Restaurant                 Hotel   

   6th Most Common Venue 7th Most Common Venue  8th Most Common Venue  \
0    Japanese Restaurant                 Hotel     Italian Restaurant   
1    Japanese Restaurant         Train Station                  Hotel   
2  Portuguese Restaurant          Skating Rink       Sushi Restaurant   
3                    Gym     French Restaurant  Vietnamese Restaurant   
4    Japanese Restaurant          Burger Joint     Italian Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0   Dumpling Restaurant       Tapas Restaurant  
1    Italian Restaurant              Juice Bar  
2    Chinese Restaurant     Falafel Restaurant  
3                  Park  Australian Restaurant  
4  Fast Food Restaurant      Convenience Store

In [44]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(melbourne_merged['Lat'], melbourne_merged['Long'], melbourne_merged['Suburb'], melbourne_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## 5. Examine Clusters

## Cluster 1

In [49]:
melbourne_merged.loc[melbourne_merged['Cluster Labels'] == 0, melbourne_merged.columns[[2] + list(range(5, melbourne_merged.shape[1]))]]

Suburb    Long  Cluster Labels  \
0                    Melbourne  144.97               0   
2               West Melbourne  144.94               0   
3        St Kilda Road Central  144.98               0   
4           World Trade Centre  144.95               0   
6                    Southbank  144.97               0   
7                    Docklands  144.95               0   
8      University Of Melbourne  144.96               0   
9                    Footscray  144.90               0   
10                      Seddon  144.90               0   
11                 Seddon West  144.90               0   
15              West Footscray  144.85               0   
16                  Yarraville  144.89               0   
21          Williamstown North  144.90               0   
23                    Seaholme  144.83               0   
24                   Braybrook  144.86               0   
26                    Robinson  144.86               0   
29              Sunshine North  144.82               0   
30               Sunshine West  144.82               0   
32                      Kealba  144.77               0   
33                      Ardeer  144.80               0   
34              Deer Park East  144.80               0   
35                    Burnside  144.75               0   
36            Burnside Heights  144.75               0   
37                    Cairnlea  144.75               0   
38            Caroline Springs  144.75               0   
45                 Altona East  144.86               0   
47                Altona North  144.86               0   
48              Laverton North  144.80               0   
49            Williams Landing  144.76               0   
50              Altona Meadows  144.78               0   
53            Hoppers Crossing  144.70               0   
54                     Tarneit  144.70               0   
55                   Truganina  144.70               0   
56                     Cocoroc  144.58               0   
57                    Derrimut  144.58               0   
58                  Point Cook  144.58               0   
59                    Quandong  144.58               0   
60                    Werribee  144.58               0   
61              Werribee South  144.58               0   
62                  Flemington  144.93               0   
64              Highpoint City  144.92               0   
65                 Maribyrnong  144.92               0   
66                  Travancore  144.92               0   
67                 Keilor East  144.80               0   
68            Avondale Heights  144.82               0   
69                      Keilor  144.83               0   
71                 Calder Park  144.78               0   
72                     Delahey  144.78               0   
73                    Hillside  144.78               0   
74                Taylors Hill  144.78               0   
76                Keilor Lodge  144.81               0   
77               Taylors Lakes  144.81               0   
80                  Aberfeldie  144.90               0   
81                    Essendon  144.90               0   
82               Essendon West  144.90               0   
83             Essendon Fields  144.91               0   
84              Essendon North  144.91               0   
85                  Strathmore  144.91               0   
86          Strathmore Heights  144.91               0   
87                Airport West  144.89               0   
88                 Keilor Park  144.89               0   
90              Gladstone Park  144.88               0   
91                   Gowanbrae  144.88               0   
92                 Tullamarine  144.88               0   
93                 Pascoe Vale  144.94               0   
94           Pascoe Vale South  144.94               0   
95           Melbourne Airport  144.83               0   
96                    Hadfield  144.92               0   
97                    

## Cluster 2

In [50]:
melbourne_merged.loc[melbourne_merged['Cluster Labels'] == 1, melbourne_merged.columns[[2] + list(range(5, melbourne_merged.shape[1]))]]

Suburb    Long  Cluster Labels  \
13             Kingsville West  144.85               1   
14                   Maidstone  144.85               1   
17             Yarraville West  144.89               1   
18            South Kingsville  144.88               1   
19                   Spotswood  144.88               1   
20                Williamstown  144.90               1   
27                      Albion  144.82               1   
28                    Glengala  144.82               1   
31                   Albanvale  144.77               1   
39                   Deer Park  144.75               1   
40             Deer Park North  144.75               1   
41                   Ravenhall  144.75               1   
42                   Mambourin  144.56               1   
43              Mount Cottrell  144.56               1   
44                Wyndham Vale  144.56               1   
51                    Laverton  144.78               1   
52                    Seabrook  144.78               1   
63                  Ascot Vale  144.92               1   
70                Keilor North  144.83               1   
98                Broadmeadows  144.92               1   
99                      Dallas  144.92               1   
119             Brunswick East  144.98               1   
126                   Moreland  144.96               1   
144            Northcote South  145.00               1   
171                  Kingsbury  145.07               1   
173                    Banyule  145.09               1   
188                  Yarrambat  145.13               1   
194            Bend Of Islands  145.28               1   
195            Kangaroo Ground  145.28               1   
196              Arthurs Creek  145.22               1   
201                     Cotham  145.04               1   
207                    Bulleen  145.08               1   
214                  The Pines  145.19               1   
218           North Warrandyte  145.22               1   
219                 Warrandyte  145.22               1   
220              Park Orchards  145.21               1   
221                 Wonga Park  145.27               1   
226             Richmond North  145.01               1   
228               Auburn South  145.05               1   
229           Glenferrie South  145.05               1   
230                   Hawthorn  145.05               1   
231             Hawthorn North  145.05               1   
236            Camberwell West  145.06               1   
240         Surrey Hills South  145.12               1   
244         Surrey Hills North  145.10               1   
248                Wattle Park  145.12               1   
257                 Nunawading  145.18               1   
272              Croydon South  145.28               1   
273                    Kilsyth  145.31               1   
278              Hoddles Creek  145.54               1   
280                    Seville  145.54               1   
287             Domain Road Po  144.06               1   
290                     Toorak  145.00               1   
291                   Armadale  145.02               1   
294                    Malvern  145.03               1   
295              Malvern North  145.03               1   
296             Caulfield East  145.04               1   
306           Chadstone Centre  145.08               1   
308                Jordanville  145.08               1   
311                     Syndal  145.13               1   
316           Knox City Centre  145.24               1   
317                  Studfield  145.24               1   
324                Lysterfield  145.30               1   
328                      Upwey  145.33               1   
337                  Caulfield  145.03               1   
338            Caulfield South  145.03               1   
346                Coatesville  145.06               1   
347                 Hughesdale  145.08               1   
349                   

## Cluster 3

In [52]:
melbourne_merged.loc[melbourne_merged['Cluster Labels'] == 2, melbourne_merged.columns[[2] + list(range(5, melbourne_merged.shape[1]))]]

Suburb    Long  Cluster Labels  \
5                   South Wharf  144.97               2   
12                   Kingsville  144.85               2   
22                       Altona  144.83               2   
46                  Altona Gate  144.86               2   
75                 Keilor Downs  144.81               2   
78                 Watergardens  144.81               2   
79                 Moonee Ponds  144.92               2   
89                      Niddrie  144.89               2   
101                    Coolaroo  144.93               2   
105    Royal Melbourne Hospital  144.96               2   
123                      Coburg  144.96               2   
140           Collingwood North  144.98               2   
147            Northland Centre  145.03               2   
148                     Preston  145.03               2   
149               Preston Lower  145.03               2   
190                 Montmorency  145.12               2   
191                Eltham North  145.15               2   
206                   Greythorn  145.07               2   
208               Bulleen South  145.08               2   
209                 Templestowe  145.12               2   
224               Burnley North  145.01               2   
259               Mitcham North  145.19               2   
264              Ringwood North  145.23               2   
269               Ringwood East  145.25               2   
270               Croydon Hills  145.28               2   
288                 South Yarra  144.06               2   
289                   Hawksburn  145.00               2   
309              Mount Waverley  145.13               2   
310                    Pinewood  145.13               2   
312                Brandon Park  145.17               2   
314               Wheelers Hill  145.17               2   
319              Wantirna South  145.24               2   
321             Bayswater North  145.27               2   
330                       Selby  145.40               2   
334                      Tecoma  145.36               2   
335          Caulfield Junction  145.31               2   
336             Caulfield North  145.31               2   
363            Noble Park North  145.18               2   
430                Pines Forest  145.19               2   
432                  Heatherton  145.21               2   
433                   Bentleigh  145.04               2   
436                   Patterson  145.04               2   
849                    Rockbank  144.69               2   
853                Toolern Vale  144.59               2   
2264                   Kalorama  145.37               2   
2269               Dixons Creek  145.32               2   
2270               Steels Creek  145.32               2   
2286              Mount Burnett  145.49               2   
2297                  The Patch  145.39               2   

      1st Most Common Venue 2nd Most Common Venue      3rd Most Common Venue  \
5                       Bar               Theater                Art Gallery   
12            Women's Store                   Zoo                Flower Shop   
22       Italian Restaurant       Harbor / Marina                Pizza Place   
46     Gym / Fitness Center           Pizza Place              Grocery Store   
75     Fast Food Restaurant         Shopping Mall             Sandwich Place   
78     Fast Food Restaurant         Shopping Mall             Sandwich Place   
79                     Café   Japanese Restaurant                        Pub   
89    Portuguese Restaurant      Department Store       Fast Food Restaurant   
101   Portuguese Restaurant           Gas Station  Middle Eastern Restaurant   
105                    Café           Pizza Place                Coffee Shop   
123      Light Rail Station         Train Station                     Market   
140                    Café                   Bar               Cocktail Bar   
147        Department Store     El

## Cluster 4

In [53]:
melbourne_merged.loc[melbourne_merged['Cluster Labels'] == 3, melbourne_merged.columns[[2] + list(range(5, melbourne_merged.shape[1]))]]

Suburb    Long  Cluster Labels 1st Most Common Venue  \
25      Braybrook North  144.86               3  Gym / Fitness Center   
100              Jacana  144.92               3  Fast Food Restaurant   
114         Moonee Vale  144.94               3    Light Rail Station   
210   Templestowe Lower  145.10               3          Home Service   
211           Doncaster  145.12               3           Golf Course   
212      Doncaster East  145.19               3           Coffee Shop   
326       Mountain Gate  145.30               3          Burger Joint   
852         Melton West  144.59               3            Restaurant   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
25             Restaurant           Supermarket                   Gym   
100      Department Store        Sandwich Place           Supermarket   
114                  Park                  Café                   Zoo   
210            Skate Park                   Zoo        Farmers Market   
211                  Park                   Zoo           Flea Market   
212         Bowling Green                  Park                   Zoo   
326         Train Station                  Café           Flower Shop   
852                  Park           Flea Market  Fast Food Restaurant   

    5th Most Common Venue   6th Most Common Venue 7th Most Common Venue  \
25          Go Kart Track  Furniture / Home Store            Food Truck   
100         Shopping Mall        Basketball Court     Electronics Store   
114           Flower Shop     Filipino Restaurant     Fish & Chips Shop   
210  Fast Food Restaurant                   Field   Filipino Restaurant   
211                 Field     Filipino Restaurant     Fish & Chips Shop   
212           Flower Shop     Filipino Restaurant     Fish & Chips Shop   
326  Fast Food Restaurant                   Field   Filipino Restaurant   
852                 Field     Filipino Restaurant     Fish & Chips Shop   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
25                    Pub         Shopping Mall     Italian Restaurant  
100          Liquor Store           Pizza Place             Donut Shop  
114           Fish Market           Flea Market      Food & Drink Shop  
210     Fish & Chips Shop           Fish Market            Flea Market  
211           Fish Market           Flower Shop         Farmers Market  
212           Fish Market           Flea Market      Food & Drink Shop  
326     Fish & Chips Shop           Fish Market            Flea Market  
852           Fish Market           Flower Shop     Falafel Restaurant

## Cluster 5

In [54]:
melbourne_merged.loc[melbourne_merged['Cluster Labels'] == 4, melbourne_merged.columns[[2] + list(range(5, melbourne_merged.shape[1]))]]

Suburb    Long  Cluster Labels 1st Most Common Venue  \
1         East Melbourne  144.99               4                   Pub   
163         Ivanhoe East  145.04               4                  Café   
166   Heidelberg Heights  145.05               4                  Café   
168      Heidelberg West  145.05               4                  Café   
169            Mill Park  145.06               4          Burger Joint   
170             Bundoora  145.07               4           Supermarket   
246       Box Hill South  145.12               4    Chinese Restaurant   
379       St Kilda South  144.98               4                  Café   
380        St Kilda West  144.98               4                  Café   
381            Balaclava  145.00               4   Japanese Restaurant   
382        St Kilda East  145.00               4   Japanese Restaurant   

    2nd Most Common Venue 3rd Most Common Venue  4th Most Common Venue  \
1                    Café           Coffee Shop         Breakfast Spot   
163           Pizza Place   Japanese Restaurant            Supermarket   
166  Gym / Fitness Center  Fast Food Restaurant            Flower Shop   
168  Gym / Fitness Center  Fast Food Restaurant            Flower Shop   
169              Pharmacy         Grocery Store          Shopping Mall   
170          Dessert Shop         Shopping Mall             Sports Bar   
246      Asian Restaurant   Dumpling Restaurant                   Café   
379                   Bar           Pizza Place  Australian Restaurant   
380                   Bar           Pizza Place  Australian Restaurant   
381                   Pub           Coffee Shop                   Café   
382                   Pub           Coffee Shop                   Café   

             5th Most Common Venue  6th Most Common Venue  \
1                  Thai Restaurant    Japanese Restaurant   
163           Fast Food Restaurant         Sandwich Place   
166                          Field    Filipino Restaurant   
168                          Field    Filipino Restaurant   
169                    Pizza Place      Fish & Chips Shop   
170                  Bowling Alley             Food Truck   
246              Korean Restaurant  Vietnamese Restaurant   
379  Vegetarian / Vegan Restaurant                 Bakery   
380  Vegetarian / Vegan Restaurant                 Bakery   
381              Convenience Store       Sushi Restaurant   
382              Convenience Store       Sushi Restaurant   

     7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
1            Train Station                 Hotel    Italian Restaurant   
163            Coffee Shop         Shopping Mall            Restaurant   
166      Fish & Chips Shop           Fish Market           Flea Market   
168      Fish & Chips Shop           Fish Market           Flea Market   
169       Basketball Court                  Café     Food & Drink Shop   
170             Food Stand            Food Court      Football Stadium   
246                 Bakery   Szechuan Restaurant           Supermarket   
379           Burger Joint         Burrito Place        Farmers Market   
380           Burger Joint         Burrito Place        Farmers Market   
381  Vietnamese Restaurant        Breakfast Spot                   Bar   
382  Vietnamese Restaurant        Breakfast Spot                   Bar   

    10th Most Common Venue  
1                Juice Bar  
163   Arts & Entertainment  
166                    Zoo  
168                    Zoo  
169            Flower Shop  
170         Farmers Market  
246            Coffee Shop  
379                   Park  
380                   Park  
381            Pizza Place  
382            Pizza Place

# Examine the Primary Schools in Melbourne

In [56]:
## Connecting to the Url and Checking the status
response = requests.get("https://bettereducation.com.au/school/Primary/vic/vic_top_primary_schools.aspx")
response.status_code

200

In [63]:
## Using Pandas and BeautifulSoup to Parse Table from the site

soup = BeautifulSoup(response.content,'html.parser')

table = soup.find_all('table')
table = table[0]

## Initialise empty column header list and df list
columns_headers = []
df = []

## Capture the column headings from the table

columns_headers = ['School','Postcode','State Overall Score','Total Enrolments' ,'Trend / Compare','Sector']
        
## Capture the table rows data

for tr in table.find_all('tr'):
    td = tr.find_all('td')
    row = [tr.text.strip() for tr in td if tr.text.strip()]
    if row:
        df.append(row)
school_data = pd.DataFrame(df,columns=columns_headers)
school_data.drop(columns='Trend / Compare',inplace=True)
school_data.head()

School Postcode  \
0      Presbyterian Ladies' College,Burwood,VIC,3125     3125   
1  St Andrews Christian College,Wantirna South,VI...     3152   
2                        Burwood East Primary School     3151   
3        Huntingtower School,Mount Waverley,VIC,3149     3149   
4            Haileybury College,Keysborough,VIC,3173     3173   

  State Overall Score Total Enrolments          Sector  
0                 100             1412  Non-government  
1                 100              581  Non-government  
2                 100              274      Government  
3                 100              686  Non-government  
4                 100             3754  Non-government

In [64]:
## To Extract the Name of the School
new = school_data['School'].str.split("," , n=2, expand = True)

In [65]:
school_data['School'] = new[0]

In [66]:
school_data.head()

School Postcode State Overall Score Total Enrolments  \
0  Presbyterian Ladies' College     3125                 100             1412   
1  St Andrews Christian College     3152                 100              581   
2   Burwood East Primary School     3151                 100              274   
3           Huntingtower School     3149                 100              686   
4            Haileybury College     3173                 100             3754   

           Sector  
0  Non-government  
1  Non-government  
2      Government  
3  Non-government  
4  Non-government

In [67]:
## Merging Postcode and Schools Dataframe

school_data = pd.merge(melbourne_data,school_data, on='Postcode')
school_data.head()

## Converting State Overall Score Column to numeric so that it can be used to Sort the Dataframe

school_data['State Overall Score'] = pd.to_numeric(school_data['State Overall Score'])
school_data = school_data.sort_values(by='State Overall Score',ascending=False)
school_data.head()

Postcode   District               Suburb State    Lat    Long  \
678     3152  Melbourne     Knox City Centre   VIC -37.87  145.24   
326     3103  Melbourne               Balwyn   VIC -37.81  145.08   
365     3109  Melbourne   Tunstall Square Po   VIC -37.81  145.19   
664     3150  Melbourne        Wheelers Hill   VIC -37.88  145.17   
786     3173  Melbourne          Keysborough   VIC -37.99  145.15   

                            School  State Overall Score Total Enrolments  \
678   St Andrews Christian College                  100              581   
326          Fintona Girls' School                  100              456   
365  Beverley Hills Primary School                  100              473   
664         Glendal Primary School                  100              873   
786             Haileybury College                  100             3754   

             Sector  
678  Non-government  
326  Non-government  
365      Government  
664      Government  
786  Non-government

In [68]:
## Creating a Dataframe with Top 10 Government Primary Schools

Gov_Schools = school_data.loc[school_data['Sector'] == 'Government']
Gov_Schools.reset_index(drop=True,inplace=True)
Gov_Schools = Gov_Schools[:10]
Gov_Schools.head(100)

Postcode   District               Suburb State    Lat    Long  \
0     3109  Melbourne   Tunstall Square Po   VIC -37.81  145.19   
1     3150  Melbourne        Wheelers Hill   VIC -37.88  145.17   
2     3167  Melbourne       Oakleigh South   VIC -37.93  145.10   
3     3150  Melbourne        Glen Waverley   VIC -37.88  145.17   
4     3150  Melbourne        Glen Waverley   VIC -37.88  145.17   
5     3150  Melbourne         Brandon Park   VIC -37.88  145.17   
6     3150  Melbourne        Wheelers Hill   VIC -37.88  145.17   
7     3109  Melbourne   Tunstall Square Po   VIC -37.81  145.19   
8     3150  Melbourne         Brandon Park   VIC -37.88  145.17   
9     3109  Melbourne            The Pines   VIC -37.81  145.19   

                             School  State Overall Score Total Enrolments  \
0     Beverley Hills Primary School                  100              473   
1            Glendal Primary School                  100              873   
2     Oakleigh South Primary School                  100             1006   
3         Mount View Primary School                  100             1083   
4            Glendal Primary School                  100              873   
5            Glendal Primary School                  100              873   
6         Mount View Primary School                  100             1083   
7  Doncaster Gardens Primary School                  100              681   
8         Mount View Primary School                  100             1083   
9  Doncaster Gardens Primary School                  100              681   

       Sector  
0  Government  
1  Government  
2  Government  
3  Government  
4  Government  
5  Government  
6  Government  
7  Government  
8  Government  
9  Government

In [69]:
## Creating a Dataframe with Top 10 Non - Government Primary Schools

NonGov_Schools = school_data.loc[school_data['Sector'] == 'Non-government']
NonGov_Schools.reset_index(drop=True,inplace=True)
#NonGov_Schools = df_Gov_Schools[:10]
NonGov_Schools.head(100)

Postcode   District                  Suburb State    Lat    Long  \
0      3152  Melbourne        Knox City Centre   VIC -37.87  145.24   
1      3103  Melbourne                  Balwyn   VIC -37.81  145.08   
2      3173  Melbourne             Keysborough   VIC -37.99  145.15   
3      3152  Melbourne          Wantirna South   VIC -37.87  145.24   
4      3152  Melbourne          Wantirna South   VIC -37.87  145.24   
5      3149  Melbourne          Mount Waverley   VIC -37.88  145.13   
6      3152  Melbourne        Knox City Centre   VIC -37.87  145.24   
7      3149  Melbourne                Pinewood   VIC -37.88  145.13   
8      3122  Melbourne           Hawthorn West   VIC -37.84  145.05   
9      3122  Melbourne           Hawthorn West   VIC -37.84  145.05   
10     3122  Melbourne            Auburn South   VIC -37.84  145.05   
11     3122  Melbourne            Auburn South   VIC -37.84  145.05   
12     3122  Melbourne        Glenferrie South   VIC -37.84  145.05   
13     3122  Melbourne        Glenferrie South   VIC -37.84  145.05   
14     3122  Melbourne                Hawthorn   VIC -37.84  145.05   
15     3122  Melbourne                Hawthorn   VIC -37.84  145.05   
16     3122  Melbourne          Hawthorn North   VIC -37.84  145.05   
17     3149  Melbourne                  Syndal   VIC -37.88  145.13   
18     3122  Melbourne          Hawthorn North   VIC -37.84  145.05   
19     3068  Melbourne            Clifton Hill   VIC -37.79  144.99   
20     3185  Melbourne               Ripponlea   VIC -37.88  145.00   
21     3125  Melbourne      Surrey Hills South   VIC -37.84  145.12   
22     3152  Melbourne               Studfield   VIC -37.87  145.24   
23     3126  Melbourne         Camberwell East   VIC -37.84  145.09   
24     3152  Melbourne                Wantirna   VIC -37.87  145.24   
25     3068  Melbourne           Fitzroy North   VIC -37.79  144.99   
26     3185  Melbourne              Gardenvale   VIC -37.88  145.00   
27     3103  Melbourne             Balwyn East   VIC -37.81  145.08   
28     3152  Melbourne                Wantirna   VIC -37.87  145.24   
29     3185  Melbourne             Elsternwick   VIC -37.88  145.00   
30     3126  Melbourne         Camberwell East   VIC -37.84  145.09   
31     3125  Melbourne            Bennettswood   VIC -37.84  145.12   
32     3152  Melbourne               Studfield   VIC -37.87  145.24   
33     3930  Melbourne             Mount Eliza   VIC -38.19  145.08   
34     3930  Melbourne                 Kunyung   VIC -38.19  145.08   
35     3142  Melbourne               Hawksburn   VIC -37.84  145.00   
36     3141  Melbourne     Chapel Street North   VIC -36.99  144.06   
37     3136  Melbourne           Croydon South   VIC -37.80  145.28   
38     3141  Melbourne          Domain Road Po   VIC -36.99  144.06   
39     3136  Melbourne           Croydon North   VIC -37.80  145.28   
40     3141  Melbourne             South Yarra   VIC -36.99  144.06   
41     3136  Melbourne           Croydon Hills   VIC -37.80  145.28   
42     3142  Melbourne                  Toorak   VIC -37.84  145.00   
43     3143  Melbourne                Armadale   VIC -37.86  145.02   
44     3143  Melbourne          Armadale North   VIC -37.86  145.02   
45     3135  Melbourne           Ringwood East   VIC -37.82  145.25   
46     3135  Melbourne               Heathmont   VIC -37.82  145.25   
47     3135  Melbourne            Bedford Road   VIC -37.82  145.25   
48     3146  Melbourne               Glen Iris   VIC -37.85  145.07   
49     3185  Melbourne             Elsternwick   VIC -37.88  145.00   
50     3029  Melbourne        Hoppers Crossing   VIC -37.88  144.70   
51     3184  Melbourne           Brighton Road   VIC -37.88  145.00   
52     3161  Melbourne      Caulfield Junction   VIC -38.03  145.31   
53     3161  Melbourne         Caulfield North   VIC -38.03  145.31   
54     3187  Melbourne              North Road   VIC -37.90  145.00   
55     3033  Melbourne     